# Análise dos locais de origem dos medalhistas brasileiros
A criação deste notebook foi feita logo após o término das Olimpíadas de 2020, após se verificar nas notícias correntes qual era o local de origem dos medalhistas que estavam sendo premiados.<br>
Aqui se desenvolveu:<br>
- Um levantamento de quais os municípios, Estados e regiões nos quais nasceram todos os medalhistas olímpicos que o Brasil já teve, desde o início dos Jogos Olímpicos até a edição de 2020 (32a edição, realizada em 2021)
- Demonstração desse resultado (soma cumulativa de medalhas) em 2 mapas, cujo conteúdo é selecionável por `widgets`:
    - <b>Mapa 1</b>: <b>"Distribuição das medalhas por Estado"</b> ou <b>"Distribuição das medalhas por região"</b> dos medalhistas, conforme a seleção pelo método `widgets.Dropdown`, mostrando-se um mapa dos 27 Estados (UF's) ou das 5 regiões, coloridos conforme a quantidade total de atletas que já ganharam medalhas, considerando-se todas as edições dos jogos.
    - <b>Mapa 2</b>: <b>"Municípios que já tiveram ao menos 1 medalhista olímpico"</b>, com separação da visualização com foco no país inteiro, com foco por região ou por Estado (UF).
- Demonstração da evolução temporal (edição a edição) desse resultado por meio de 4 gráficos de barras do tipo `bar_chart_race`:
    - <b>Barchart 1: "Estados de origem dos medalhistas olímpicos do Brasil": </b>um gráfico contendo a soma cumulativa simples (sem pesos) de todas as medalhas ganhas por pessoas originárias de cada Estado (UF) do Brasil.
    - <b>Barchart 2: "Regiões de origem dos medalhistas olímpicos do Brasil": </b>um gráfico contendo a soma cumulativa simples (sem pesos) de todas as medalhas ganhas por pessoas originárias de cada região (conforme o traçado atual) do Brasil.
    - <b>Barchart 3: "Cidades de origem dos medalhistas olímpicos do Brasil": </b>um gráfico contendo a soma cumulativa simples (sem pesos) de todas as medalhas ao Brasil ganhas por pessoas originárias de cada cidade, usando-se o conjunto total de municípios e incluindo-se as cidades de nascimento de pessoas nascidas no exterior, mas que competiram pelo Brasil.
    - <b>Barchart 4: "Cidades de origem dos medalhistas olímpicos do Brasil (Excluindo-se capitais e cidades das suas regiões metropolitanas)": </b>um gráfico contendo a soma cumulativa simples (sem pesos) de todas as medalhas ao Brasil ganhas por pessoas originárias de cada cidade, incluindo-se as cidades de nascimento de pessoas nascidas no exterior, mas que competiram pelo Brasil, porém excluindo-se as capitais estaduais e municípios de regiões metropolitanas do Brasil.

Para se fazer os mapas, aplicou-se um peso sobre as medalhas. Maiores detalhes na seção `Função de pesos das medalhas e dos esportes`.<br> 
1. <b>Peso por hierarquia das medalhas:</b> ouro, prata e bronze possuem pesos diferentes.
2. <b>Peso por equipe:</b> medalhas obtidas por atletas de esportes individuais possuem pesos diferentes de medalhas obtidas por atletas que fizeram parte de uma equipe.

Foram usadas as seguintes fontes de dados:<br>
<b>Lista de medalhistas até 2016: Kaggle - "120 years of Olympic history: athletes and results"</b><br>
Link: https://www.kaggle.com/datasets/heesoo37/120-years-of-olympic-history-athletes-and-results
<br><br><b>Lista de medalhistas de 2020: WikiPedia - "Brasil nos Jogos Olímpicos de Verão de 2020"</b><br>
Link: https://pt.wikipedia.org/wiki/Brasil_nos_Jogos_Ol%C3%ADmpicos_de_Ver%C3%A3o_de_2020
<br><br><b>Mapas do Brasil: IBGE (Instituto Brasileiro de Geografia e Estatística) - Malha Municipal</b><br>Link: https://www.ibge.gov.br/geociencias/organizacao-do-territorio/malhas-territoriais/15774-malhas.html?=&t=acesso-ao-produto
<br>Link direto dos mapas: https://geoftp.ibge.gov.br/organizacao_do_territorio/malhas_territoriais/malhas_municipais/municipio_2021/Brasil/BR/BR_Municipios_2021.zip

<b>Principais bibliotecas e conhecimentos utilizados:</b><br>
`geopandas`: confecção dos mapas mostrados e leitura do arquivo `.shp` (extraído de um arquivo `.zip` online), com as informações cartográficas sobre a malha municipal do Brasil. Entendimento dos dados de geometrias, sobreposição de diferentes camadas de mapas e também de utilização do valor de um parâmetro como grau de colorização em um mapa de cores (`column = coluna_desejada`).<br>
`matplotlib`: as principais propriedades para visualização dos mapas, como as cores (`cmap`, por exemplo), propriedades de labels, títulos, etc, foram ajustado com essa biblioteca.<br>
`ipywidgets`: biblioteca que foi usada para se fazer seleção dinâmica de qual mapa específico o usuário deseja ver dentro de uma figura, dispensando-se plotar várias figuras.<br>
`bar_chart_race`: biblioteca usada para se gerar os gráficos em barras do tipo `bar_chart_race`. Para se poder utilizar o método `bar_chart_race` desta biblioteca, é preciso fazer uma seqüência de ajustes à base de dados e aqui neste notebook temos um exemplo. Pode-se tanto mostrar o gráfico `bar_chart_race` dentro do Jupyter Notebook, como exportá-lo a um arquivo de vídeo. Para isto, basta ajustar o parâmetro `filename`. Caso seja `filename = None`, o gráfico será mostrado dentro do Notebook.Caso se faça uma declaração de `filename = 'nome_desejado.mp4`, então será feita uma exportação do gráfico a um arquivo chamado `nome_desejado.mp4`. Como um exemplo, aqui neste Jupyter Notebook exportou-se um gráfico com o nome de `Medalhistas_por_cidade_interior.mp4`.<br>
`pandas` e `numpy`: análises fundamentais das tabelas e principais cálculos.
<br><br>
Para se salvar o mapa da malha municipal, do site do IBGE, por meio de um webscraping simples:<br>
`urllib`: abrir um site dentro de um código em Python. Por meio do método `urlopen` do pacote `urllib.request`, abre-se uma página web.<br>
`zipfile`: extrair online um arquivo `.zip`, por meio do método `ZipFile`.<br>
`io`: aqui, usou-se para salvar um arquivo em disco.
`shutil`: aqui, usou-se para apagar um diretório do disco (método `rmtree`).

<b>Análise de features:</b> Para se poder mostrar nos mapas e gráficos uma informação que faça algum sentido ao usuário/leitor final, é preciso fazer uma seleção e análise de features, e não apenas usar-se os dados brutos. Algumas das principais:
- Inclusão de informação sobre Estado (UF) de origem e região<br>
- Criação de uma métrica de pesos associadas a cada medalha ganha, com base em hierarquia da medalha (ouro, prata, bronze) e com base na quantidade de participantes de cada esporte (individual ou em equipe).
- Exclusão de dados sobre atletas que competiram por outros países.

<b>Limpeza de dados:</b> Para se poder realizar correlações entre diferentes fontes de dados sobre os atletas e também se mostrar uma informação correta, fez-se limpeza de dados nos nomes dos atletas.

<b>Maiores detalhes sobre a </b>`bar_chart_race`:<br>
Documentação: https://pypi.org/project/bar-chart-race/<br>
Um link com exemplos e instruções de uso: https://towardsdatascience.com/a-single-python-function-generating-a-gorgeous-bar-chart-race-video-dd6410b8aed<br>
Um segundo link com exemplos e instruções de uso: https://www.kaggle.com/code/firefortysix/bar-chart-race-of-global-coffee-production/notebook

## Importação das bibliotecas

In [1]:
import pandas as pd
import numpy as np
import geopandas as gpd
import matplotlib.pyplot as plt
plt.rcParams["font.serif"] = "cmr10"

# Serão usadas para se mostrar widgets
import ipywidgets as widgets
from IPython.display import display

%matplotlib inline

In [2]:
import bar_chart_race as bcr
import warnings
warnings.filterwarnings("ignore")

## Definição das funções

In [3]:
# Função específica para se baixar e ler o mapa do Brasil em granularidade por municípios, oferecida pelo IBGE
# Esta função temporariamente irá baixar a base de arquivos e apagá-la logo em seguida
def Leitura_Mapa_BR_Mun():
    from io import BytesIO
    from zipfile import ZipFile
    from urllib.request import urlopen
    
    # Baixa o arquivo .zip com os mapas diretamente do site do IBGE
    resp = urlopen('https://geoftp.ibge.gov.br/organizacao_do_territorio/malhas_territoriais/malhas_municipais/municipio_2021/Brasil/BR/BR_Municipios_2021.zip')

    zipfile = ZipFile(BytesIO(resp.read()))
    
    # Extrai temporariamente todos os arquivos do .zip em um diretório chamado 'mapas/BR_Municipios_2021/'
    zipfile.extractall('mapas/BR_Municipios_2021/')
    
    # Faz-se a leitura do GeoDataFrame:
    gpd_mapa = gpd.read_file('mapas/BR_Municipios_2021/BR_Municipios_2021.shp', encoding = 'utf-8')
    
    # Apaga-se o diretório e os arquivos baixados, após se conseguir gravar o GeoDataFrame
    import shutil
    shutil.rmtree('mapas/BR_Municipios_2021')
    
    return gpd_mapa

In [4]:
# Função para diversas correções pontuais nos nomes
# Correção feita com base em um dicionário
def Nomes_Datas_Nasc(nome_corrigir, parametro):
    
    dict_correcoes = {"Adenzia Aparecida Ferreira da Silva":"Adenízia Aparecida Ferreira da Silva", 
"Adriana \"Adrianinha\" Moiss Pinto":"Adriana \"Adrianinha\" Moisés Pinto", 
"Adriana dos Santos Arajo":"Adriana dos Santos Araújo", 
"Afonso de Azevedo vora":"Affonso de Azevedo Évora", 
"Afrnio Antnio da Costa":"Afrânio Antônio da Costa", 
"Aldair Nascimento dos Santos":"Aldair Santos do Nascimento", 
"Alexander Welter":"Alexandre Welter", 
"Alosio Pires Alves":"Aloísio Pires Alves", 
"Amaury Antnio Pasos":"Amaury Antônio Pasos", 
"Ana Flvia Chritaro Daniel Sanglard":"Ana Flávia Chritaro Daniel Sanglard", 
"Ana Ida Margarita  Alvarez Vieira":"Ana Margarida \"Ida\" Vieira Álvares", 
"Andr Alves da Cruz":"André Alves da Cruz", 
"Andr Bier Johannpeter":"André Bier Gerdau Johannpeter", 
"Andr Domingos da Silva":"André Domingos da Silva", 
"Andr Felipe \"Pampa\" Falbo Ferreira":"André Felipe \"Pampa\" Falbo Ferreira", 
"Andr Heller":"André Heller", 
"Andr Luiz da Silva Nascimento":"André Luiz da Silva Nascimento", 
"Andr Luiz Moreira":"André Luiz Moreira", 
"Andr Lus dos Santos Ferreira":"André Luís dos Santos Ferreira", 
"Andria \"Maycon\" dos Santos":"Andréia \"Maycon\" dos Santos", 
"Andria Rosa de Andrade":"Andréia Rosa de Andrade", 
"Andria Suntaque":"Andréia Suntaque", 
"Antnio Carlos \"Badalhoca\" Gueiros Ribeiro":"Antônio Carlos \"Badalhoca\" Gueiros Ribeiro", 
"Antnio Carlos \"Carlo\" Aguilar Gouveia":"Antônio Carlos \"Carlo\" Aguilar Gouveia", 
"Antnio Jos \"Tonho\" Gil":"Antônio José \"Tonho\" Gil", 
"Antnio Salvador Sucar":"Antônio Salvador Sucar", 
"Aurlio Fernndez Miguel":"Aurélio Fernández Miguel", 
"Brbara Micheline do Monte Barbosa":"Bárbara Micheline do Monte Barbosa", 
"Bruno Lins Tenrio de Barros":"Bruno Lins Tenório de Barros", 
"Bruno Uvini Bortolana":"Bruno Uvini Bortolança", 
"Cludia Maria \"Cludinha\" das Neves":"Cláudia Maria \"Claudinha\" das Neves", 
"Cludia Maria Pastor":"Cláudia Maria Pastor", 
"Cludio Andr Mergen Taffarel":"Cláudio André Mergen Taffarel", 
"Cludio Roberto de Sousa":"Cláudio Roberto Souza", 
"Cntia Silva dos Santos":"Cíntia Silva dos Santos", 
"Csar Augusto Cielo Filho":"César Augusto Cielo Filho", 
"Dante Guimares Santos do Amaral":"Dante Guimarães Santos do Amaral", 
"David \"Davi\" Cortez Silva":"David \"Davi\" Cortes da Silva", 
"Delma \"Pretinha\" Gonalves":"Delma \"Pretinha\" Gonçalves", 
"der Francis Carbonera":"Éder Francis Carbonera", 
"Diego Matias Hyplito":"Diego Matias Hypólito", 
"Domingos \"Domingos Maracan\" Lampariello Neto":"Domingos \"Domingos Maracanã\" Lampariello Neto", 
"Edvaldo Valrio da Silva Filho":"Edvaldo Valério da Silva Filho", 
"Elisngela Almeida de Oliveira":"Elisângela Almeida de Oliveira", 
"Ericlia \"Fil\" Bodziak":"Ericléia \"Filó\" Bodziak", 
"Esquiva Falco Florentino":"Esquiva Falcão Florentino", 
"Evandro Motta Guerra":"Evandro Motta Marcondes Guerra", 
"Fabiana da Silva Simes":"Fabiana da Silva Simões", 
"Felipe Anderson Perieira Gomes":"Felipe Anderson Pereira Gomes", 
"Fernando \"Fernando Brobr\" Pereira de Freitas":"Fernando \"Fernando Brobró\" Pereira de Freitas", 
"Fernando \"Fernando\" Roscio de vila":"Fernando \"Fernandão\" Roscio de Ávila", 
"Flvio da Conceio":"Flávio da Conceição", 
"Flvio Vianna de Ulha Canto":"Flávio Vianna De Ulhôa Canto", 
"Gilmar Lus Rinaldi":"Gilmar Luís Rinaldi", 
"Giovane Farinazzo Gvio":"Giovane Farinazzo Gávio", 
"Givanildo \"Hulk\" Vieira de Souza":"Givanildo \"Hulk\" Vieira de Sousa", 
"Grazielle Pinheiro Guimares Nascimento":"Grazielle Pinheiro Guimarães Nascimento", 
"Gustavo Frana Borges":"Gustavo França Borges", 
"Henrique Carlos Serra Azul Guimares":"Henrique Carlos Serra Azul Guimarães", 
"Hlia \"Fofo\" Rogrio de Souza Pinto":"Hélia \"Fofão\" Rogério de Souza Pinto", 
"Hortncia Maria de Ftima Marcari Oliva":"Hortência Maria de Fátima Marcari Oliva", 
"Janina Dia Chagas da Conceio":"Janina Déia Chagas da Conceição", 
"Joo \"J\" Alves de Assis Silva":"João \"Jô\" Alves de Assis Silva", 
"Joo \"Kita\" Leithardt Neto":"João \"Kita\" Leithardt Neto", 
"Joo Carlos de Oliveira":"João Carlos de Oliveira", 
"Joo Francisco Brz":"João Francisco Bráz", 
"Joo Santos Batista":"João Batista Viana Santos", 
"Jorge Jos \"Jorginho\" de Amorim Campos":"Jorge José \"Jorginho\" de Amorim Campos", 
"Jorge Luiz Andrade da Silva":"Jorge Luís Andrade da Silva", 
"Jos Carlos Cracco Neto":"José Carlos Cracco Neto", 
"Jos Carlos Gomes Moreira":"José Carlos Gomes Moreira", 
"Jos Edvar Simes":"José Edvar Simões", 
"Jos Elias \"Z Elias\" Moedim Jnior":"José Elias \"Zé Elias\" Moedim Júnior", 
"Jos Ferreira Neto":"José Ferreira Neto", 
"Jos Marcelo \"Z Maria\" Ferreira":"José Marcelo \"Zé Maria\" Ferreira", 
"Jos Montanaro Jnior":"José Montanaro Júnior", 
"Jos Roberto \"Bebeto\" Gama de Oliveira":"José Roberto \"Bebeto\" Gama de Oliveira", 
"Jos Telles da Conceio":"José Telles da Conceição", 
"Kelly Silva dos Santos":"Kelly da Silva Santos", 
"Ktia Andreia Caldeira Lopes":"Kátia Andreia Caldeira Lopes", 
"Leandro Damio da Silva dos Santos":"Leandro Damião da Silva dos Santos", 
"Lilian Cristina Lopes Gonalves":"Lilian Cristina Lopes Gonçalves", 
"Luiz Carlos \"Luizo\" Bombonato Goulart":"Luiz Carlos \"Luizão\" Bombonato Goulart", 
"Luiz Felipe Cortizo Gonalves de Azevedo":"Luiz Felipe Cortizo Gonçalves de Azevedo", 
"Lus Carlos Coelho Winck":"Luís Carlos Coelho Winck", 
"Manuel dos Santos Filho":"Manoel dos Santos Júnior", 
"Marcelo Jos \"Marcelinho Paulista\" de Souza":"Marcelo José \"Marcelinho Paulista\" de Souza", 
"Marcelo Teles Negro":"Marcelo Teles Negrão", 
"Marcelo Vieira da Silva Jnior":"Marcelo Vieira da Silva Júnior", 
"Marcos \"Marquinhos\" Aos Corra":"Marcos \"Marquinhos\" Aoás Corrêa", 
"Marcus Vincius Dias":"Marcus Vinícius Dias", 
"Marcus Vincius Freire Simes":"Marcus Vinícius Simões Freire", 
"Maria Anglica \"Branca\" Gonalves da Silva":"Maria Angélica \"Branca\" Gonçalves da Silva", 
"Maria Paula Gonalves da Silva":"Maria Paula Gonçalves da Silva", 
"Maurcio Borges Almeida Silva":"Maurício Borges Almeida Silva", 
"Maurcio Camargo Lima":"Maurício Camargo Lima", 
"Maurcio Luiz de Souza":"Maurício Luiz de Souza", 
"Maurine Dorneles Gonalves":"Maurine Dorneles Gonçalves", 
"Mauro Geraldo Galvo":"Mauro Geraldo Galvão", 
"Mlton Cruz":"Milton Cruz", 
"Mlton de Souza Filho":"Milton Luiz de Souza Filho", 
"Mnica Anglica de Paula":"Mônica Angélica de Paula", 
"Moyss Bls":"Moysés Blás", 
"Mrcia Regina \"Mrcia Fu\" Cunha":"Márcia Regina \"Márcia Fu\" Cunha", 
"Mrcio Rafael \"Rafinha\" Ferreira de Souza":"Márcio Rafael \"Rafinha\" Ferreira de Souza", 
"Mrio \"Xand\" de Oliveira Neto":"Mário \"Xandó\" de Oliveira Neto", 
"Natlia Falavigna Silva":"Natália Falavigna Silva", 
"Natlia Zlio Pereira":"Natália Zílio Pereira", 
"nderson Lus de Abreu Oliveira":"Anderson Luís de Abreu Oliveira", 
"Nelson de Jess \"Dida\" Silva":"Nelson de Jesus \"Dida\" Silva", 
"Nelson Falco":"Nelson Falcão", 
"Neymar da Silva Santos Jnior":"Neymar da Silva Santos Júnior", 
"Nlson Prudncio":"Nelson Prudêncio", 
"Oscar dos Santos Emboaba Jnior":"Oscar dos Santos Emboaba Júnior", 
"Oswaldo \"Juninho Paulista\" Giroldo Jnior":"Oswaldo \"Juninho Paulista\" Giroldo Júnior", 
"Paulo Andr \"Paulo\" Jukoski da Silva":"Paulo André \"Paulão\" Jukoski da Silva", 
"Paulo Henrique \"Ganso\" Chagas de Lima":"Paulo Henrique \"Ganso\" de Chagas Lima", 
"Rafael Alcntara do Nascimento":"Rafael Alcântara do Nascimento", 
"Rafael Augusto Sbis do Nascimento":"Rafael Augusto Sóbis do Nascimento", 
"Raquel Peluci Xavier da Silva":"Raquel Peluci Xavier Camargo da Silva", 
"Rbson Caetano da Silva":"Robson Caetano da Silva", 
"Renata Aparacida \"Kki\" da Costa":"Renata Aparecida \"Kóki\" da Costa", 
"rika Cristiano dos Santos":"Érika Cristiano dos Santos", 
"rika Kelly \"Kiki\" Pereira Coimbra":"Érika Kelly \"Kiki\" Pereira Coimbra", 
"Rmulo Borges Monteiro":"Rômulo Borges Monteiro", 
"Robson Donato Conceio":"Robson Donato Conceição", 
"Rodrigo \"Rodrigo\" Santana":"Rodrigo \"Rodrigão\" Santana", 
"Rogrio Sampaio Cardoso":"Rogério Sampaio Cardoso", 
"Romrio de Souza Faria":"Romário de Souza Faria", 
"Ronaldo \"Ronaldinho\" de Asss Moreira":"Ronaldo \"Ronaldinho\" de Assis Moreira", 
"Ronaldo Luiz Nazrio \"Ronaldinho\" de Lima":"Ronaldo Luiz Nazário \"Ronaldinho\" de Lima", 
"Ronaldo Morais Silva":"Ronaldo Moraes Silva", 
"Sandro Raniere Guimares Cordeiro":"Sandro Ranieri Guimarães Cordeiro", 
"Sebastio Wolf":"Sebastião Wolf", 
"Servilio Sebastio de Oliveira":"Servílio Sebastião de Oliveira", 
"Sidnei \"Sido\" dos Santos Junior":"Sidnei \"Sidão\" dos Santos Junior", 
"Simone Gomes Jatob":"Simone Gomes Jatobá", 
"Srgio \"Escadinha\" Dutra dos Santos":"Sérgio \"Escadinha\" Dutra dos Santos", 
"Srgio \"Srgio Macarro\" de Toledo Machado":"Sérgio \"Sérgio Macarrão\" Toledo Machado", 
"Srgio Lus \"Joo Paulo\" Donizetti":"Sérgio Luís \"João Paulo\" Donizetti", 
"Svio Pimentel Bortolini":"Sávio Bortolini Pimentel", 
"Thasa Daher de Menezes":"Thaísa Daher de Menezes", 
"Tnia Maria \"Tnia Maranho\" Pereira Ribeiro":"Tânia Maria \"Tânia Maranhão\" Pereira Ribeiro", 
"Vicente Lenlson de Lima":"Vicente Lenílson de Lima", 
"Victor Borba \"Rivaldo\" Ferreira":"Rivaldo Victor Borba Ferreira", 
"Welissa \"Sass\" de Souza Gonzaga":"Wélissa \"Sassá\" de Souza Gonzaga", 
"Wlter Carmona":"Walter Carmona", 
"Wverton Pereira da Silva":"Weverton Pereira da Silva", 
"Yamaguchi Falco Florentino":"Yamaguchi Falcão Florentino", 
"Yane Mrcia Campos da Fonseca Marques":"Yane Márcia Campos da Fonseca Marques", 
"Zenny \"Algodo\" de Azevedo":"Zenny \"Algodão\" de Azevedo", 
}
    
    dict_locais_nasc = {'Ademir Roque Kaefer':['Toledo', 'Paraná'],
'Adenízia Aparecida Ferreira da Silva':['Ibiaí', 'Minas Gerais'],
'Adhemar Ferreira da Silva':['São Paulo', 'São Paulo'],
'Adriana "Adrianinha" Moisés Pinto':['Franca', 'São Paulo'],
'Adriana Aparecida dos Santos':['São Bernardo do Campo', 'São Paulo'],
'Adriana dos Santos Araújo':['Salvador', 'Bahia'],
'Affonso de Azevedo Évora':['Rio de Janeiro', 'Rio de Janeiro'],
'Afrânio Antônio da Costa':['Macaé', 'Rio de Janeiro'],
'Alberto Marson':['Casa Branca', 'São Paulo'],
'Aldair Santos do Nascimento':['Ilhéus', 'Bahia'],
'Alessandra dos Santos de Oliveira':['São Paulo', 'São Paulo'],
'Alex Sandro da Silva':['Amparo', 'São Paulo'],
'Alex Sandro Lobo Silva':['Catanduva', 'São Paulo'],
'Alexandre Welter':['São Paulo', 'São Paulo'],
'Alexandre "Alexandre Pato" Rodrigues da Silva':['Pato Branco', 'Paraná'],
'Alexandre "Amaral" da Silva Mariano':['Capivari', 'São Paulo'],
'Alexandre "Tande" Ramos Samuel':['Resende', 'Rio de Janeiro'],
'Alexandre Gemignani Ferreira':['São Paulo', 'São Paulo'],
'Alfredo Rodrigues da Motta':['Rio de Janeiro', 'Rio de Janeiro'],
'Aline Pellegrino':['São Paulo', 'São Paulo'],
'Aloísio Pires Alves':['Pelotas', 'Rio Grande do Sul'],
'Alvaro Affonso "Doda" de Miranda Neto':['São Paulo', 'São Paulo'],
'Amauri Ribeiro':['São Paulo', 'São Paulo'],
'Amaury Antônio Pasos':['São Paulo', 'São Paulo'],
'Ana Beatriz Moser':['Blumenau', 'Santa Catarina'],
'Ana Flávia Chritaro Daniel Sanglard':['Belo Horizonte', 'Minas Gerais'],
'Ana Margarida "Ida" Vieira Álvares':['São Paulo', 'São Paulo'],
'Ana Paula Rodrigues Connelly (-Rodrigues Henkel)':['Lavras', 'Minas Gerais'],
'Anderson de Oliveira Rodrigues':['Belo Horizonte', 'Minas Gerais'],
'Anderson Hernanes de Carvalho Andrade Lima':['Recife', 'Pernambuco'],
'André Alves da Cruz':['Piracicaba', 'São Paulo'],
'André Bier Gerdau Johannpeter':['Porto Alegre', 'Rio Grande do Sul'],
'André Domingos da Silva':['Santo André', 'São Paulo'],
'André Felipe "Pampa" Falbo Ferreira':['Recife', 'Pernambuco'],
'André Heller':['Novo Hamburgo', 'Rio Grande do Sul'],
'André Luiz da Silva Nascimento':['São João de Meriti', 'Rio de Janeiro'],
'André Luiz Moreira':['São Paulo', 'São Paulo'],
'André Luís dos Santos Ferreira':['Porto Alegre', 'Rio Grande do Sul'],
'Andréia "Maycon" dos Santos':['Lages', 'Santa Catarina'],
'Andréia Rosa de Andrade':['São Pedro do Turvo', 'São Paulo'],
'Andréia Suntaque':['Nova Cantu', 'Paraná'],
'Antônio Carlos "Badalhoca" Gueiros Ribeiro':['Rio de Janeiro', 'Rio de Janeiro'],
'Antônio Carlos "Carlo" Aguilar Gouveia':['Rio Branco', 'Acre'],
'Antônio José "Tonho" Gil':['Criciúma', 'Santa Catarina'],
'Antônio Salvador Sucar':['Lules', 'Exterior'],
'Arnaldo de Oliveira da Silva':['Rio de Janeiro', 'Rio de Janeiro'],
'Arthur Nabarrete Zanetti':['São Caetano do Sul', 'São Paulo'],
'Arthur Nory Oyakawa Mariano':['Campinas', 'São Paulo'],
'Augilmar "Gilmar Popoca" Silva de Oliveira':['Manaus', 'Amazonas'],
'Aurélio Fernández Miguel':['São Paulo', 'São Paulo'],
'Bernard Rajzman':['Rio de Janeiro', 'Rio de Janeiro'],
'Bernardo "Bernardinho" Rocha de Rezende':['Rio de Janeiro', 'Rio de Janeiro'],
'Bárbara Micheline do Monte Barbosa':['Recife', 'Pernambuco'],
'Breno Vinicius Rodrigues Borges':['Cruzeiro', 'São Paulo'],
'Bruno "Bruninho" Mossa de Rezende':['Rio de Janeiro', 'Rio de Janeiro'],
'Bruno Lins Tenório de Barros':['Maceió', 'Alagoas'],
'Bruno Prada':['São Paulo', 'São Paulo'],
'Bruno Uvini Bortolança':['Capivari', 'São Paulo'],
'Burkhard Cordes':['Darmstadt', 'Exterior'],
'Carlos "Mosquito" Domingos Massoni':['São Paulo', 'São Paulo'],
'Carlos Alberto Borges Jayme':['Goiânia', 'Goiás'],
'Carlos Caetano "Dunga" Bledorn Verri':['Ijuí', 'Rio Grande do Sul'],
'Carlos Eduardo Honorato':['São Paulo', 'São Paulo'],
'Carmo "Rosa Branca" de Souza':['Araraquara', 'São Paulo'],
'Carolina "Carol" Demartini de Albuquerque':['Porto Alegre', 'Rio Grande do Sul'],
'Chiaki Ishii':['Ashikaga', 'Exterior'],
'Claudinei Quirino da Silva':['Lençóis Paulista', 'São Paulo'],
'Clinio Freitas':['Niterói', 'Rio de Janeiro'],
'Cláudia Maria "Claudinha" das Neves':['Guarujá', 'São Paulo'],
'Cláudia Maria Pastor':['Barão de Cocais', 'Minas Gerais'],
'Cláudio André Mergen Taffarel':['Santa Rosa', 'Rio Grande do Sul'],
'Cláudio Roberto Souza':['Teresina', 'Piauí'],
'Cíntia Silva dos Santos':['Mauá', 'São Paulo'],
'Cristiane Rozeira de Souza Silva':['Osasco', 'São Paulo'],
'César Augusto Cielo Filho':['Santa Bárbara d\'Oeste', 'São Paulo'],
'Cyro Marques Delgado':['União da Vitória', 'Paraná'],
'Daniel Adler':['Rio de Janeiro', 'Rio de Janeiro'],
'Daniela Alves Lima':['São Paulo', 'São Paulo'],
'Danielle "Dani" Rodrigues Lins':['Recife', 'Pernambuco'],
'Danilo Luiz da Silva':['Bicas', 'Minas Gerais'],
'Dante Guimarães Santos do Amaral':['Itumbiara', 'Goiás'],
'Dario Barbosa':['Porto Alegre', 'Rio Grande do Sul'],
'David "Davi" Cortes da Silva':['Rio de Janeiro', 'Rio de Janeiro'],
'Delma "Pretinha" Gonçalves':['Rio de Janeiro', 'Rio de Janeiro'],
'Éder Francis Carbonera':['Farroupilha', 'Rio Grande do Sul'],
'Diego Matias Hypólito':['Santo André', 'São Paulo'],
'Diego Ribas da Cunha':['Ribeirão Preto', 'São Paulo'],
'Djan Garrido Madruga':['Santos', 'São Paulo'],
'Domingos "Domingos Maracanã" Lampariello Neto':['São Paulo', 'São Paulo'],
'Douglas Chiarotti':['Santo André', 'São Paulo'],
'Douglas Correia de Souza':['Santa Bárbara d\'Oeste', 'São Paulo'],
'Douglas dos Santos Justino de Melo':['João Pessoa', 'Paraíba'],
'Douglas Eduardo Vieira':['Londrina', 'Paraná'],
'Edmar Bernardes dos Santos':['Araxá', 'Minas Gerais'],
'Edson "Edson Bispo" Bispo dos Santos':['Rio de Janeiro', 'Rio de Janeiro'],
'Edson Luciano Ribeiro':['Bandeirantes', 'Paraná'],
'Eduardo Henrique Gomes Penido':['Rio de Janeiro', 'Rio de Janeiro'],
'Edvaldo Valério da Silva Filho':['Salvador', 'Bahia'],
'Elaine Estrela Moura':['Salvador', 'Bahia'],
'Elisângela Almeida de Oliveira':['Londrina', 'Paraná'],
'Ericléia "Filó" Bodziak':['Curitiba', 'Paraná'],
'Erlon de Souza Silva':['Ubatã', 'Bahia'],
'Esquiva Falcão Florentino':['Vitória', 'Espírito Santo'],
'Ester Aperecida dos Santos':['São Paulo', 'São Paulo'],
'Evandro Motta Marcondes Guerra':['Ibirá', 'São Paulo'],
'Fabiana "Fabi" Alvim de Oliveira':['Rio de Janeiro', 'Rio de Janeiro'],
'Fabiana da Silva Simões':['Salvador', 'Bahia'],
'Fabiana Marcelino Claudino':['Santa Luzia', 'Minas Gerais'],
'Felipe Almeida Wu':['São Paulo', 'São Paulo'],
'Felipe Anderson Pereira Gomes':['Brasília', 'Distrito Federal'],
'Felipe Eidji Kitadai':['São Paulo', 'São Paulo'],
'Fernanda "Fernandinha" Ferreira':['Rio de Janeiro', 'Rio de Janeiro'],
'Fernanda Garay Rodrigues':['Porto Alegre', 'Rio Grande do Sul'],
'Fernanda Porto Venturini':['Araraquara', 'São Paulo'],
'Fernanda Ryff Moreira Oliveira':['Porto Alegre', 'Rio Grande do Sul'],
'Fernando "Fernando Brobró" Pereira de Freitas':['Niterói', 'Rio de Janeiro'],
'Fernando "Fernandão" Roscio de Ávila':['São Paulo', 'São Paulo'],
'Fernando "Xuxa" de Queiroz Scherer':['Florianópolis', 'Santa Catarina'],
'Fernando Soledade':['Rio de Janeiro', 'Rio de Janeiro'],
'Flávio da Conceição':['Santa Maria da Serra', 'São Paulo'],
'Flávio Vianna De Ulhôa Canto':['Oxford', 'Exterior'],
'Francielle Manoel Alberto':['São Paulo', 'São Paulo'],
'Francisco Carlos "Chico" Martins Vidal':['Rio Brilhante', 'Mato Grosso do Sul'],
'Friedrich Wilhelm "Fritz" Braun':['Rio de Janeiro', 'Rio de Janeiro'],
'Gabriel Barbosa Almeida':['São Bernardo do Campo', 'São Paulo'],
'Gabriel Fernando de Jesus':['São Paulo', 'São Paulo'],
'Gabriel Vasconcellos Ferreira':['Unaí', 'Minas Gerais'],
'Geovani Faria da Silva':['Vitória', 'Espírito Santo'],
'Gilberto Amauri "Giba" de Godoy Filho':['Londrina', 'Paraná'],
'Gilmar Luís Rinaldi':['Erechim', 'Rio Grande do Sul'],
'Giovane Farinazzo Gávio':['Juiz de Fora', 'Minas Gerais'],
'Givanildo "Hulk" Vieira de Sousa':['Campina Grande', 'Paraíba'],
'Grazielle Pinheiro Guimarães Nascimento':['Brasília', 'Distrito Federal'],
'Guilherme Paraense':['Belém', 'Pará'],
'Gustavo Endres':['Passo Fundo', 'Rio Grande do Sul'],
'Gustavo França Borges':['Ituverava', 'São Paulo'],
'Hamilton "Careca" de Souza':['Passos', 'Minas Gerais'],
'Helen Cristina Santos Luz':['Araçatuba', 'São Paulo'],
'Henrique "Kiko" Pellicano':['Rio de Janeiro', 'Rio de Janeiro'],
'Henrique Carlos Serra Azul Guimarães':['São Paulo', 'São Paulo'],
'Hilma Aparecida Caldeira':['Diamantina', 'Minas Gerais'],
'Hélia "Fofão" Rogério de Souza Pinto':['São Paulo', 'São Paulo'],
'Hortência Maria de Fátima Marcari Oliva':['Potirendaba', 'São Paulo'],
'Ilisaine Karen "Zaine" David':['Jundiaí', 'São Paulo'],
'Ilson Pereira "Ilsinho" Dias Jnior':['São Bernardo do Campo', 'São Paulo'],
'Isabel Marques Swan':['Rio de Janeiro', 'Rio de Janeiro'],
'Isaquias Queiroz dos Santos':['Ubaitaba', 'Bahia'],
'Janelson dos Santos Carvalho':['Porto Alegre', 'Rio Grande do Sul'],
'Janeth dos Santos Arcain':['Carapicuíba', 'São Paulo'],
'Janina Déia Chagas da Conceição':['Rio de Janeiro', 'Rio de Janeiro'],
'Jaqueline Maria "Jaque" Pereira de Carvalho Endres':['Recife', 'Pernambuco'],
'Jatyr Eduardo Schall':['São Paulo', 'São Paulo'],
'Joaquim Carvalho Cruz':['Taguatinga', 'Distrito Federal'],
'João "Jô" Alves de Assis Silva':['São Paulo', 'São Paulo'],
'João "Kita" Leithardt Neto':['Passo Fundo', 'Rio Grande do Sul'],
'João Carlos de Oliveira':['Pindamonhangaba', 'São Paulo'],
'João Francisco Bráz':['São Paulo', 'São Paulo'],
'João Batista Viana Santos':['Uberlândia', 'Minas Gerais'],
'Jorge Edson Souza de Brito':['Porto Alegre', 'Rio Grande do Sul'],
'Jorge José "Jorginho" de Amorim Campos':['Rio de Janeiro', 'Rio de Janeiro'],
'Jorge Luiz "Pinga" Brum da Silva':['Porto Alegre', 'Rio Grande do Sul'],
'Jorge Luís Andrade da Silva':['Juiz de Fora', 'Minas Gerais'],
'Jorge Luiz Fernandes Leite':['Rio de Janeiro', 'Rio de Janeiro'],
'José Carlos Cracco Neto':['Paranavaí', 'Paraná'],
'José Carlos Gomes Moreira':['Codó', 'Maranhão'],
'José Edvar Simões':['São José dos Campos', 'São Paulo'],
'José Elias "Zé Elias" Moedim Júnior':['São Paulo', 'São Paulo'],
'José Ferreira Neto':['Santo Antônio de Posse', 'São Paulo'],
'José Marcelo "Zé Maria" Ferreira':['Oeiras', 'Piauí'],
'José Montanaro Júnior':['São Paulo', 'São Paulo'],
'José Roberto "Bebeto" Gama de Oliveira':['Salvador', 'Bahia'],
'José Telles da Conceição':['Rio de Janeiro', 'Rio de Janeiro'],
'Juan Guilherme Nunes Jesus':['Belo Horizonte', 'Minas Gerais'],
'Juliana Ribeiro Cabral':['São Paulo', 'São Paulo'],
'Kahena Kunze':['São Paulo', 'São Paulo'],
'Karin Rodrigues':['São Paulo', 'São Paulo'],
'Kelly Cristina Pereira da Silva':['Rio de Janeiro', 'Rio de Janeiro'],
'Kelly da Silva Santos':['São Paulo', 'São Paulo'],
'Kely Kolasco Fraga':['Belo Horizonte', 'Minas Gerais'],
'Ketleyn Lima Quadros':['Ceilândia', 'Distrito Federal'],
'Kátia Andreia Caldeira Lopes':['Barranquilla', 'Exterior'],
'Lars Schmidt Grael':['São Paulo', 'São Paulo'],
'Lars Sigurd Bjorkstrom':['Gotemburgo', 'Exterior'],
'Leandro Damião da Silva dos Santos':['Jardim Alegre', 'Paraná'],
'Leandro Marques Guilheiro':['Suzano', 'São Paulo'],
'Leandro Vissotto Neves':['Rio de Janeiro', 'Rio de Janeiro'],
'Leila de Gomes de Barros':['Brasília', 'Distrito Federal'],
'Leila de Souza Sobral Freitas':['São Paulo', 'São Paulo'],
'Lilian Cristina Lopes Gonçalves':['Sorocaba', 'São Paulo'],
'Luan Garcia Teixeira':['Vitória', 'Espírito Santo'],
'Luan Guilherme de Jesus Vieira':['São José do Rio Preto', 'São Paulo'],
'Lucas Pezzini Leiva':['Dourados', 'Mato Grosso do Sul'],
'Lucas Rodrigues Moura da Silva':['São Paulo', 'São Paulo'],
'Lucas Saatkamp':['Colinas', 'Rio Grande do Sul'],
'Luiz Carlos "Luizão" Bombonato Goulart':['Rubinéia', 'São Paulo'],
'Luiz Felipe Cortizo Gonçalves de Azevedo':['Rio de Janeiro', 'Rio de Janeiro'],
'Luiz Felipe Marques Fonteles':['Curitiba', 'Paraná'],
'Luiz Yoshio Onmura':['São Paulo', 'São Paulo'],
'Luís Carlos Coelho Winck':['Portão', 'Rio Grande do Sul'],
'Maicon de Andrade Siqueira':['Justinópolis', 'Minas Gerais'],
'Manoel dos Santos Júnior':['Guararapes', 'São Paulo'],
'Marcelo "Marcelinho" Elgarten':['Rio de Janeiro', 'Rio de Janeiro'],
'Marcelo Bastos Ferreira':['Niterói', 'Rio de Janeiro'],
'Marcelo José "Marcelinho Paulista" de Souza':['Cotia', 'São Paulo'],
'Marcelo Teles Negrão':['São Paulo', 'São Paulo'],
'Marcelo Vieira da Silva Júnior':['Rio de Janeiro', 'Rio de Janeiro'],
'Marcos "Marquinhos" Aoás Corrêa':['São Paulo', 'São Paulo'],
'Marcos Pinto Rizzo Soares':['Rio de Janeiro', 'Rio de Janeiro'],
'Marcus Laborne Mattioli':['Belo Horizonte', 'Minas Gerais'],
'Marcus Vinícius Dias':['Rio de Janeiro', 'Rio de Janeiro'],
'Marcus Vinícius Simões Freire':['Bento Gonçalves', 'Rio Grande do Sul'],
'Maria Angélica "Branca" Gonçalves da Silva':['Osvaldo Cruz', 'São Paulo'],
'Maria Paula Gonçalves da Silva':['Osvaldo Cruz', 'São Paulo'],
'Marianne "Mari" Steinbrecher':['São Paulo', 'São Paulo'],
'Marta de Souza Sobral':['São Paulo', 'São Paulo'],
'Marta Vieira da Silva':['Dois Riachos', 'Alagoas'],
'Martine Soffiatti Grael':['Niterói', 'Rio de Janeiro'],
'Massinet Sorcinelli':['São Paulo', 'São Paulo'],
'Maurício Borges Almeida Silva':['Maceió', 'Alagoas'],
'Maurício Camargo Lima':['Campinas', 'São Paulo'],
'Maurício Luiz de Souza':['Iturama', 'Minas Gerais'],
'Maurine Dorneles Gonçalves':['Rio Grande', 'Rio Grande do Sul'],
'Mauro Geraldo Galvão':['Porto Alegre', 'Rio Grande do Sul'],
'Maurren Higa Maggi':['São Carlos', 'São Paulo'],
'Mayra Aguiar da Silva':['Porto Alegre', 'Rio Grande do Sul'],
'Miraildes "Formiga" Maciel Mota':['Salvador', 'Bahia'],
'Milton Cruz':['Cubatão', 'São Paulo'],
'Milton Luiz de Souza Filho':['Rio de Janeiro', 'Rio de Janeiro'],
'Mônica Angélica de Paula':['São Carlos', 'São Paulo'],
'Moysés Blás':['Belo Horizonte', 'Minas Gerais'],
'Márcia Regina "Márcia Fu" Cunha':['Juiz de Fora', 'Minas Gerais'],
'Márcio Rafael "Rafinha" Ferreira de Souza':['Londrina', 'Paraná'],
'Mário "Xandó" de Oliveira Neto':['Poços de Caldas', 'Minas Gerais'],
'Murilo Endres':['Passo Fundo', 'Rio Grande do Sul'],
'Nalbert Tavares Bitencourt':['Rio de Janeiro', 'Rio de Janeiro'],
'Narciso dos Santos':['Neópolis', 'Sergipe'],
'Natália Falavigna Silva':['Maringá', 'Paraná'],
'Natália Zílio Pereira':['Ponta Grossa', 'Paraná'],
'Anderson Luís de Abreu Oliveira':['Porto Alegre', 'Rio Grande do Sul'],
'Nelson de Jesus "Dida" Silva':['Irará', 'Bahia'],
'Nelson Falcão':['Rio de Janeiro', 'Rio de Janeiro'],
'Neymar da Silva Santos Júnior':['Mogi das Cruzes', 'São Paulo'],
'Nilton Pacheco de Oliveira':['Salvador', 'Bahia'],
'Nelson Prudêncio':['Lins', 'São Paulo'],
'Norberto Murara Neto':['Araxá', 'Minas Gerais'],
'Oscar dos Santos Emboaba Júnior':['Americana', 'São Paulo'],
'Oswaldo "Juninho Paulista" Giroldo Júnior':['São Paulo', 'São Paulo'],
'Paula Renata Marques Pequeno':['Brasília', 'Distrito Federal'],
'Paulo André "Paulão" Jukoski da Silva':['Porto Alegre', 'Rio Grande do Sul'],
'Paulo dos Santos':['Porto Alegre', 'Rio Grande do Sul'],
'Paulo Henrique "Ganso" de Chagas Lima':['Ananindeua', 'Pará'],
'Peter Ficker':['São Paulo', 'São Paulo'],
'Poliana Okimoto-Cintra':['São Paulo', 'São Paulo'],
'Rafael Alcântara do Nascimento':['São Paulo', 'São Paulo'],
'Rafael Augusto Sóbis do Nascimento':['Erechim', 'Rio Grande do Sul'],
'Rafael Carlos da Silva':['Campo Grande', 'Mato Grosso do Sul'],
'Rafael Pereira da Silva':['Petrópolis', 'Rio de Janeiro'],
'Rafaela Lopes Silva':['Rio de Janeiro', 'Rio de Janeiro'],
'Ramires Santos do Nascimento':['Barra do Piraí', 'Rio de Janeiro'],
'Raquel Peluci Xavier Camargo da Silva':['Rio de Janeiro', 'Rio de Janeiro'],
'Robson Caetano da Silva':['Rio de Janeiro', 'Rio de Janeiro'],
'Reinaldo Conrad':['São Paulo', 'São Paulo'],
'Renan Brito Soares':['Viamão', 'Rio Grande do Sul'],
'Renan dal Zotto':['São Leopoldo', 'Rio Grande do Sul'],
'Renata Aparecida "Kóki" da Costa':['Assaí', 'Paraná'],
'Renato Soares de Oliveira Augusto':['Rio de Janeiro', 'Rio de Janeiro'],
'Ricarda Raquel Barbosa Lima':['Taguatinga', 'Distrito Federal'],
'Ricardo "Ricardinho" Bermudez Garcia':['São Paulo', 'São Paulo'],
'Ricardo Prado':['Andradina', 'São Paulo'],
'Ricardo Samuel Lucarelli Santos de Souza':['Contagem', 'Minas Gerais'],
'Érika Cristiano dos Santos':['São Paulo', 'São Paulo'],
'Érika Kelly "Kiki" Pereira Coimbra':['Belo Horizonte', 'Minas Gerais'],
'Rômulo Borges Monteiro':['Picos', 'Piauí'],
'Robert Scheidt':['São Paulo', 'São Paulo'],
'Roberto Carlos da Silva':['Garça', 'São Paulo'],
'Robson Donato Conceição':['Salvador', 'Bahia'],
'Rodrigo "Rodrigão" Santana':['São Paulo', 'São Paulo'],
'Rodrigo Caio Coquette Russo':['Dracena', 'São Paulo'],
'Rodrigo de Paula Pessoa':['Paris', 'Exterior'],
'Rodrigo Dourado Cunha':['Pelotas', 'Rio Grande do Sul'],
'Rogério Sampaio Cardoso':['Santos', 'São Paulo'],
'Romário de Souza Faria':['Rio de Janeiro', 'Rio de Janeiro'],
'Ronaldo "Ronaldinho" de Assis Moreira':['Porto Alegre', 'Rio Grande do Sul'],
'Ronaldo Camargo Ribeiro Senfft':['Rio de Janeiro', 'Rio de Janeiro'],
'Ronaldo Guiaro':['Piracicaba', 'São Paulo'],
'Ronaldo Luiz Nazário "Ronaldinho" de Lima':['Rio de Janeiro', 'Rio de Janeiro'],
'Ronaldo Moraes Silva':['São Paulo', 'São Paulo'],
'Rosana dos Santos Augusto':['São Paulo', 'São Paulo'],
'Roseli de Belo':['São Paulo', 'São Paulo'],
'Roseli do Carmo Gustavo':['Araraquara', 'São Paulo'],
'Rui Campos Nascimento':['Rio de Janeiro', 'Rio de Janeiro'],
'Ruy de Freitas':['Macaé', 'Rio de Janeiro'],
'Samuel Fuchs':['Curitiba', 'Paraná'],
'Sandra Maria Suruagy Lima':['Maceió', 'Alagoas'],
'Sandro Ranieri Guimarães Cordeiro':['Riachinho', 'Minas Gerais'],
'Sandro Ricardo Rodrigues Viana':['Manaus', 'Amazonas'],
'Sarah Gabrielle Cabral de Menezes':['Teresina', 'Piauí'],
'Sebastião Wolf':['Gößweinstein', 'Exterior'],
'Servílio Sebastião de Oliveira':['São Paulo', 'São Paulo'],
'Sheilla Tavares de Castro Blassioli':['Belo Horizonte', 'Minas Gerais'],
'Sidnei "Sidão" dos Santos Junior':['São Caetano do Sul', 'São Paulo'],
'Silvia Andrea "Silvinha" Santos Luz':['Araçatuba', 'São Paulo'],
'Silvio "Silvinho" Paiva':['Franca', 'São Paulo'],
'Simone Gomes Jatobá':['Maringá', 'Paraná'],
'Sérgio "Escadinha" Dutra dos Santos':['Diamente do Norte', 'Paraná'],
'Sérgio "Sérgio Macarrão" Toledo Machado':['Rio de Janeiro', 'Rio de Janeiro'],
'Sérgio Luís "João Paulo" Donizetti':['Campinas', 'São Paulo'],
'Sávio Bortolini Pimentel':['Vila Velha', 'Espírito Santo'],
'Talmo Curto de Oliveira':['Itabira', 'Minas Gerais'],
'Tandara Caixeta':['Brasília', 'Distrito Federal'],
'Tetsuo Okamoto':['Marília', 'São Paulo'],
'Thaísa Daher de Menezes':['Rio de Janeiro', 'Rio de Janeiro'],
'Thiago Braz da Silva':['Marília', 'São Paulo'],
'Thiago Emiliano da Silva':['Rio de Janeiro', 'Rio de Janeiro'],
'Thiago Machado Vilela Pereira':['Volta Redonda', 'Rio de Janeiro'],
'Thiago Maia Alencar':['Boa Vista', 'Roraima'],
'Thiago Neves Augusto':['Curitiba', 'Paraná'],
'Thiago Soares Alves':['Porto Alegre', 'Rio Grande do Sul'],
'Tiago Henrique de Oliveira Camilo':['Tupã', 'São Paulo'],
'Tânia Maria "Tânia Maranhão" Pereira Ribeiro':['São Luís', 'Maranhão'],
'Torben Schmidt Grael':['São Paulo', 'São Paulo'],
'Ubiratan "Bira" Pereira Maciel':['São Paulo', 'São Paulo'],
'Valeska "Valeskinha" dos Santos Menezes':['Niterói', 'Rio de Janeiro'],
'Vanderlei Cordeiro de Lima':['Cruzeiro do Oeste', 'Paraná'],
'Vicente Lenílson de Lima':['Currais Novos', 'Rio Grande do Norte'],
'Rivaldo Victor Borba Ferreira':['Paulista', 'Pernambuco'],
'Victor Mirshauswka':['Cherni', 'Exterior'],
'Virna Cristine Dantes Dias':['Natal', 'Rio Grande do Norte'],
'Walace Souza Silva':['Salvador', 'Bahia'],
'Waldemar Blatskauskas':['São Paulo', 'São Paulo'],
'Waldyr Geraldo Boccardo':['São Manuel', 'São Paulo'],
'Walewska Moreira de Oliveira':['Belo Horizonte', 'Minas Gerais'],
'Wallace Leandro de Souza':['Rio de Janeiro', 'Rio de Janeiro'],
'Wélissa "Sassá" de Souza Gonzaga':['Barbacena', 'Minas Gerais'],
'William Carvalho da Silva':['São Paulo', 'São Paulo'],
'William de Asevedo Furtado':['Pelotas', 'Rio Grande do Sul'],
'William Peixoto Arjona':['São Paulo', 'São Paulo'],
'Wlamir Marques':['São Vicente', 'São Paulo'],
'Walter Carmona':['São Paulo', 'São Paulo'],
'Weverton Pereira da Silva':['Rio Branco', 'Acre'],
'Yamaguchi Falcão Florentino':['São Mateus', 'Espírito Santo'],
'Yane Márcia Campos da Fonseca Marques':['Afogados da Ingazeira', 'Pernambuco'],
'Zenny "Algodão" de Azevedo':['Rio de Janeiro', 'Rio de Janeiro'],
}
    
    # CORREÇÕES DOS NOMES
    if nome_corrigir in dict_correcoes:
        nome_corrigido = dict_correcoes[nome_corrigir]
        
    else:
        nome_corrigido = nome_corrigir
    
    if parametro == 'Right name':
        return nome_corrigido
    
    # ASSIGNAÇÃO DOS LOCAIS DE NASCIMENTO
    elif parametro == 'Birthplace':
        return dict_locais_nasc[nome_corrigido][0]
    
    elif parametro == 'Birthplace_UF':
        return dict_locais_nasc[nome_corrigido][1]
    
    else:
        return 'PARÂMETRO INVÁLIDO'

## Leitura dos dados de base

In [5]:
# Leitura da lista total de medalhistas, sem incluir 2020 (lista até 2016)
total_olimp = pd.read_csv('bases/athlete_events.csv', encoding='utf-8')
total_olimp.sample(5)

ID                    Name Sex   Age  Height  Weight    Team  NOC  \
112666   57076             Yuka Kamino   F  21.0   163.0    54.0   Japan  JPN   
217043  109004           Marek Seweryn   M  22.0   160.0    63.5  Poland  POL   
150987   75771     Juan Maximo Martnez   M  21.0   165.0    53.0  Mexico  MEX   
106925   54053        Ahad Javan Saleh   M  23.0   169.0    62.0    Iran  IRI   
6676      3734  Hjalmar Johan Andersen   M  28.0     NaN     NaN  Norway  NOR   

              Games  Year  Season            City                      Sport  \
112666  2002 Winter  2002  Winter  Salt Lake City  Short Track Speed Skating   
217043  1980 Summer  1980  Summer          Moskva              Weightlifting   
150987  1968 Summer  1968  Summer     Mexico City                  Athletics   
106925  1988 Summer  1988  Summer           Seoul                  Wrestling   
6676    1952 Winter  1952  Winter            Oslo              Speed Skating   

                                                 Event   Medal  
112666  Short Track Speed Skating Women's 1,500 metres     NaN  
217043               Weightlifting Men's Featherweight  Bronze  
150987                   Athletics Men's 10,000 metres     NaN  
106925      Wrestling Men's Featherweight, Greco-Roman     NaN  
6676                 Speed Skating Men's 10,000 metres    Gold

In [6]:
# Leituras dos mapas: Estados, regiões atuais e municípios:
mapa_UF = gpd.read_file('mapas/estados_2010/estados_2010.shp')
mapa_reg = gpd.read_file('mapas/regioes_2010/regioes_2010.shp')
mapa_mun = Leitura_Mapa_BR_Mun() # Apenas a leitura do mapa com granularidade municipal será feita por uma função separada
mapa_DF = gpd.read_file("mapas/Regiao_Administrativa_do_DF_-_2019/Regiao_Administrativa_do_DF_-_2019.shp")

In [7]:
# Padronização dos sistemas de referência: todos terão o mesmo valor da base municipal pelo IBGE
mapa_UF = mapa_UF.to_crs(mapa_mun.crs)
mapa_reg = mapa_reg.to_crs(mapa_mun.crs)
mapa_DF = mapa_DF.to_crs(mapa_mun.crs)

In [8]:
# Mudanças em nomes de colunas dos geodataframes dos mapas, para melhorar os futuros merges
mapa_UF = mapa_UF.rename(columns= {'nome':'Estado'})
mapa_reg = mapa_reg.rename(columns= {'nome':'Região atual'})
mapa_mun = mapa_mun.rename(columns= {'NM_MUN':'Município'})
mapa_mun = mapa_mun.rename(columns= {'SIGLA':'SIGLA_UF'})

In [9]:
# Inclusão das cidades do Distrito Federal na lista
mapa_mun = mapa_mun[mapa_mun['SIGLA_UF'] != 'DF']
mapa_mun = mapa_mun.append(gpd.GeoDataFrame({'CD_MUN':list([5300108]* len(mapa_DF)), 'Município':mapa_DF['ra'], 'SIGLA_UF':list(['DF']* len(mapa_DF)), 'AREA_KM2':mapa_DF['geometry'].area/10**6, 'geometry':mapa_DF['geometry']}))
mapa_mun.loc[mapa_mun['Município'] == 'Plano Piloto', 'Município'] = 'Brasília'

In [10]:
# Redução do conjunto de análise apenas para os medalhistas do Brasil, 
# com a criação de um novo dataframe chamado total_medalists_BR
total_medalists = total_olimp.copy()
total_medalists = total_medalists[~(total_medalists['Medal'].isna())]
total_medalists_BR = total_medalists[total_medalists['Team'] == 'Brazil'].reset_index(drop=True)
total_medalists_BR

ID                                 Name Sex   Age  Height  Weight  \
0       918                  Ademir Roque Kaefer   M  24.0   179.0    74.0   
1       918                  Ademir Roque Kaefer   M  28.0   179.0    74.0   
2       925  Adenzia Aparecida Ferreira da Silva   F  25.0   187.0    65.0   
3       966                         Daniel Adler   M  26.0   180.0    72.0   
4      1020         Adriana Aparecida dos Santos   F  25.0   180.0    61.0   
..      ...                                  ...  ..   ...     ...     ...   
444  133931             Arthur Nabarrete Zanetti   M  22.0   156.0    61.0   
445  133931             Arthur Nabarrete Zanetti   M  26.0   156.0    61.0   
446  134186     Jos Elias "Z Elias" Moedim Jnior   M  19.0   178.0    75.0   
447  134191       Jos Marcelo "Z Maria" Ferreira   M  22.0   175.0    71.0   
448  134211               Jos Carlos Cracco Neto   M  22.0   170.0    69.0   

       Team  NOC        Games  Year  Season            City       Sport  \
0    Brazil  BRA  1984 Summer  1984  Summer     Los Angeles    Football   
1    Brazil  BRA  1988 Summer  1988  Summer           Seoul    Football   
2    Brazil  BRA  2012 Summer  2012  Summer          London  Volleyball   
3    Brazil  BRA  1984 Summer  1984  Summer     Los Angeles     Sailing   
4    Brazil  BRA  1996 Summer  1996  Summer         Atlanta  Basketball   
..      ...  ...          ...   ...     ...             ...         ...   
444  Brazil  BRA  2012 Summer  2012  Summer          London  Gymnastics   
445  Brazil  BRA  2016 Summer  2016  Summer  Rio de Janeiro  Gymnastics   
446  Brazil  BRA  1996 Summer  1996  Summer         Atlanta    Football   
447  Brazil  BRA  1996 Summer  1996  Summer         Atlanta    Football   
448  Brazil  BRA  2016 Summer  2016  Summer  Rio de Janeiro    Football   

                                   Event   Medal  
0                Football Men's Football  Silver  
1                Football Men's Football  Silver  
2          Volleyball Women's Volleyball    Gold  
3    Sailing Mixed Three Person Keelboat  Silver  
4          Basketball Women's Basketball  Silver  
..                                   ...     ...  
444               Gymnastics Men's Rings    Gold  
445               Gymnastics Men's Rings  Silver  
446              Football Men's Football  Bronze  
447              Football Men's Football  Bronze  
448              Football Men's Football    Gold  

[449 rows x 15 columns]

## Início da limpeza dos dados

In [11]:
import locale
locale.setlocale(locale.LC_ALL, "pt_BR.UTF-8")

# Criação de um dataframe name_for_corr para se corrigir e padronizar os nomes dos atletas, além de incluir locais de nascimento
# Esse dataframe depois será utilizado para corrigir o dataframe de base total_medalists_BR
name_for_corr = pd.DataFrame(sorted(total_medalists_BR['Name'].unique(), key = locale.strxfrm), columns = ['Original name'])
name_for_corr['Right name'] = name_for_corr.apply(lambda x: Nomes_Datas_Nasc(x['Original name'], 'Right name'), axis=1) 
# Right name irá conter o nome correto e 'Original name' o nome conforme a fonte original
name_for_corr['Birthplace'] = name_for_corr.apply(lambda x: Nomes_Datas_Nasc(x['Original name'], 'Birthplace'), axis=1) 
name_for_corr['Birthplace_UF'] = name_for_corr.apply(lambda x: Nomes_Datas_Nasc(x['Original name'], 'Birthplace_UF'), axis=1) 
name_for_corr

Original name  \
0                     Ademir Roque Kaefer   
1     Adenzia Aparecida Ferreira da Silva   
2               Adhemar Ferreira da Silva   
3        Adriana "Adrianinha" Moiss Pinto   
4            Adriana Aparecida dos Santos   
..                                    ...   
338                         Wlter Carmona   
339              Wverton Pereira da Silva   
340            Yamaguchi Falco Florentino   
341  Yane Mrcia Campos da Fonseca Marques   
342             Zenny "Algodo" de Azevedo   

                                Right name             Birthplace  \
0                      Ademir Roque Kaefer                 Toledo   
1     Adenízia Aparecida Ferreira da Silva                  Ibiaí   
2                Adhemar Ferreira da Silva              São Paulo   
3        Adriana "Adrianinha" Moisés Pinto                 Franca   
4             Adriana Aparecida dos Santos  São Bernardo do Campo   
..                                     ...                    ...   
338                         Walter Carmona              São Paulo   
339              Weverton Pereira da Silva             Rio Branco   
340            Yamaguchi Falcão Florentino             São Mateus   
341  Yane Márcia Campos da Fonseca Marques  Afogados da Ingazeira   
342             Zenny "Algodão" de Azevedo         Rio de Janeiro   

      Birthplace_UF  
0            Paraná  
1      Minas Gerais  
2         São Paulo  
3         São Paulo  
4         São Paulo  
..              ...  
338       São Paulo  
339            Acre  
340  Espírito Santo  
341      Pernambuco  
342  Rio de Janeiro  

[343 rows x 4 columns]

In [12]:
# Correção dos nomes no dataframe total_medalists_BR e inclusão dos locais de nascimento
name_for_corr = name_for_corr.rename(columns= {'Original name':'Name'})
total_medalists_BR = pd.merge(total_medalists_BR, name_for_corr, on='Name', how='left')
name_for_corr = name_for_corr.rename(columns= {'Name':'Original name'})
total_medalists_BR = total_medalists_BR.iloc[:,[0,15,16,17,2,3,4,5,6,7,8,9,10,11,12,13,14]]
total_medalists_BR = total_medalists_BR.rename(columns = {'Right name':'Name'})

In [13]:
total_medalists_BR.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 449 entries, 0 to 448
Data columns (total 17 columns):
 #   Column         Non-Null Count  Dtype  
---  ------         --------------  -----  
 0   ID             449 non-null    int64  
 1   Name           449 non-null    object 
 2   Birthplace     449 non-null    object 
 3   Birthplace_UF  449 non-null    object 
 4   Sex            449 non-null    object 
 5   Age            448 non-null    float64
 6   Height         432 non-null    float64
 7   Weight         422 non-null    float64
 8   Team           449 non-null    object 
 9   NOC            449 non-null    object 
 10  Games          449 non-null    object 
 11  Year           449 non-null    int64  
 12  Season         449 non-null    object 
 13  City           449 non-null    object 
 14  Sport          449 non-null    object 
 15  Event          449 non-null    object 
 16  Medal          449 non-null    object 
dtypes: float64(3), int64(2), object(12)
memory usage: 63.1

## Filtragem apenas das colunas necessárias e adição dos dados de 2020

In [14]:
# Criação de um novo dataframe birth_med_BR, que irá conter apenas as colunas necessárias para análise
birth_med_BR = total_medalists_BR.copy()
birth_med_BR = birth_med_BR[['Name', 'Sex', 'Birthplace', 'Birthplace_UF', 'Year', 'City', 'Sport', 'Event', 'Medal']]
birth_med_BR.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 449 entries, 0 to 448
Data columns (total 9 columns):
 #   Column         Non-Null Count  Dtype 
---  ------         --------------  ----- 
 0   Name           449 non-null    object
 1   Sex            449 non-null    object
 2   Birthplace     449 non-null    object
 3   Birthplace_UF  449 non-null    object
 4   Year           449 non-null    int64 
 5   City           449 non-null    object
 6   Sport          449 non-null    object
 7   Event          449 non-null    object
 8   Medal          449 non-null    object
dtypes: int64(1), object(8)
memory usage: 35.1+ KB


In [15]:
# Visualização de uma amostra dos dados
birth_med_BR.sample(10)

Name Sex   Birthplace Birthplace_UF  Year  \
212  Ana Margarida "Ida" Vieira Álvares   F    São Paulo     São Paulo  1996   
20                       Amauri Ribeiro   M    São Paulo     São Paulo  1992   
265        Marianne "Mari" Steinbrecher   F    São Paulo     São Paulo  2008   
267                      Wlamir Marques   M  São Vicente     São Paulo  1960   
8     Alessandra dos Santos de Oliveira   F    São Paulo     São Paulo  1996   
64           Hamilton "Careca" de Souza   M       Passos  Minas Gerais  1988   
335         Isaquias Queiroz dos Santos   M     Ubaitaba         Bahia  2016   
305                      Tetsuo Okamoto   M      Marília     São Paulo  1952   
33            Adriana dos Santos Araújo   F     Salvador         Bahia  2012   
199           Leandro Marques Guilheiro   M       Suzano     São Paulo  2008   

               City       Sport  \
212         Atlanta  Volleyball   
20        Barcelona  Volleyball   
265         Beijing  Volleyball   
267            Roma  Basketball   
8           Atlanta  Basketball   
64            Seoul    Football   
335  Rio de Janeiro    Canoeing   
305        Helsinki    Swimming   
33           London      Boxing   
199         Beijing        Judo   

                                             Event   Medal  
212                  Volleyball Women's Volleyball  Bronze  
20                     Volleyball Men's Volleyball    Gold  
265                  Volleyball Women's Volleyball    Gold  
267                    Basketball Men's Basketball  Bronze  
8                    Basketball Women's Basketball  Silver  
64                         Football Men's Football  Silver  
335  Canoeing Men's Canadian Doubles, 1,000 metres  Silver  
305          Swimming Men's 1,500 metres Freestyle  Bronze  
33                      Boxing Women's Lightweight  Bronze  
199                         Judo Men's Lightweight  Bronze

In [16]:
# Inclusão dos dados da Olimpíada de 2020:
birth_med_BR = pd.read_csv('bases/medal_rev.csv')

In [17]:
birth_med_BR.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 504 entries, 0 to 503
Data columns (total 9 columns):
 #   Column         Non-Null Count  Dtype 
---  ------         --------------  ----- 
 0   Name           504 non-null    object
 1   Sex            504 non-null    object
 2   Birthplace     504 non-null    object
 3   Birthplace_UF  504 non-null    object
 4   Year           504 non-null    int64 
 5   City           504 non-null    object
 6   Sport          504 non-null    object
 7   Event          504 non-null    object
 8   Medal          504 non-null    object
dtypes: int64(1), object(8)
memory usage: 35.6+ KB


## Função de pesos das medalhas e dos esportes
Aqui serão estabelecidos pesos para cada uma das medalhas conseguidas. 
<br>Resumo do critério: medalhas com melhor pontuação têm peso maior e medalhas conseguidas em equipe são consideradas como uma divisão da medalha com toda a equipe.
1. Pesos por medalha:<br>
&nbsp; Ouro: 3 pontos - peso 3<br>
 &nbsp; Prata: 2 pontos - peso 2<br>
 &nbsp; Bronze: 1 ponto - peso 1<br>
2. Pesos por equipe:<br>
&nbsp; Modalidade individual: peso 1 (100%)<br>
&nbsp; Modalidade em equipe: peso de 1/(tamanho da equipe)

In [18]:
# Criação de um novo dataframe weight_df, que conterá os pesos por modalidade
# Posteriormente, haverá merge desse dataframe com o dataframe principal
weight_df = pd.DataFrame(sorted(birth_med_BR['Event'].unique()), columns=['Event'])
weight_df['Sport'] = weight_df['Event'].str.split(expand=True)[0]
weight_df.loc[weight_df['Sport'] == 'Modern', 'Sport'] = 'Modern Pentathlon'
weight_df['In team?'] = ''
weight_df['Event weight'] = ''
weight_df

Event       Sport In team? Event weight
0             Athletics Men's 200 metres   Athletics                      
1   Athletics Men's 4 x 100 metres Relay   Athletics                      
2     Athletics Men's 400 metres hurdles   Athletics                      
3             Athletics Men's 800 metres   Athletics                      
4              Athletics Men's High Jump   Athletics                      
..                                   ...         ...      ...          ...
64           Taekwondo Men's Heavyweight   Taekwondo                      
65         Taekwondo Women's Heavyweight   Taekwondo                      
66                Tennis Women's doubles      Tennis                      
67           Volleyball Men's Volleyball  Volleyball                      
68         Volleyball Women's Volleyball  Volleyball                      

[69 rows x 4 columns]

In [19]:
# Assignação dos valores mais óbvios:

# Basquete, futebol e vôlei sempre serão em equipe, não importa em que modalidade.
# Aqui serão definido apenas que são em equipe. Os tamanhos serão ajustados posteriormente.
weight_df.loc[weight_df['Sport'] == 'Basketball', 'In team?'] = 'Yes'
weight_df.loc[weight_df['Sport'] == 'Football', 'In team?'] = 'Yes'
weight_df.loc[weight_df['Sport'] == 'Volleyball', 'In team?'] = 'Yes'
weight_df.loc[weight_df['Event'].str.contains('Team') , 'In team?'] = 'Yes'

# Boxe, judô, tiro, skate, surf e taekwondo sempre serão individuais, não importa em que modalidade.
# Aqui já se ajustam seus pesos, que deverão ter valor 1.
weight_df.loc[weight_df['Sport'] == 'Boxing', ['In team?','Event weight']] = 'No', 1
weight_df.loc[weight_df['Sport'] == 'Judo', ['In team?','Event weight']] = 'No', 1
weight_df.loc[weight_df['Sport'] == 'Shooting', ['In team?','Event weight']] = 'No', 1
weight_df.loc[weight_df['Sport'] == 'Skateboarding', ['In team?','Event weight']] = 'No', 1
weight_df.loc[weight_df['Sport'] == 'Surfing', ['In team?','Event weight']] = 'No', 1
weight_df.loc[weight_df['Sport'] == 'Taekwondo', ['In team?','Event weight']] = 'No', 1

# Qualquer modalidade que em seu nome leve as palavras 'One Person', 'Individual' ou 'Single' é individual.
# Aqui já se ajustam seus pesos, que deverão ter valor 1.
weight_df.loc[weight_df['Event'].str.contains('One Person'), ['In team?','Event weight']] = 'No', 1
weight_df.loc[weight_df['Event'].str.contains('Individual'), ['In team?','Event weight']] = 'No', 1
weight_df.loc[weight_df['Event'].str.contains('Singles'), ['In team?','Event weight']] = 'No', 1

# Qualquer modalidade que em seu nome leve as palavras 'Two Person', 'Doubles' ou 'doubles' é feita em equipes de 2 pessoas.
# Qualquer modalidade que em seu nome leve as palavras 'Three Person' é feita em equipes de 3 pessoas.
weight_df.loc[weight_df['Event'].str.contains('Two Person'), ['In team?','Event weight']] = 'Yes', 1/2
weight_df.loc[weight_df['Event'].str.contains('Three Person'), ['In team?','Event weight']] = 'Yes', 1/3
weight_df.loc[weight_df['Event'].str.contains('Doubles'), ['In team?','Event weight']] = 'Yes', 1/2
weight_df.loc[weight_df['Event'].str.contains('doubles'), ['In team?','Event weight']] = 'Yes', 1/2

In [20]:
# Associações após análises
weight_df.loc[weight_df['Sport'] == 'Modern Pentathlon', ['In team?','Event weight']] = 'No', 1
weight_df.loc[weight_df['Event'] == "Swimming Men's 4 x 100 metres Freestyle Relay", ['In team?','Event weight']] = 'Yes', 1/4
weight_df.loc[weight_df['Event'] == "Swimming Men's 4 x 200 metres Freestyle Relay", ['In team?','Event weight']] = 'Yes', 1/4
weight_df.loc[weight_df['Event'] == "Athletics Men's 4 x 100 metres Relay", ['In team?','Event weight']] = 'Yes', 1/4

# ESPECIFICAMENTE PARA O ANO 2000, O PESO DE "Athletics Men's 4 x 100 metres Relay" DEVERÁ SER 1/5, EM VEZ DE 1/4
# CORRIGE-SE LOGO À FRENTE, APÓS OS MERGES

weight_df.loc[weight_df['Event'] == "Sailing Mixed Multihull", ['In team?','Event weight']] = 'Yes', 1/2
weight_df.loc[weight_df['Event'] == "Sailing Women's Skiff", ['In team?','Event weight']] = 'Yes', 1/2

weight_df.loc[((weight_df['Sport'] == "Athletics") & (weight_df['In team?'] == '')), ['In team?','Event weight']] = 'No', 1
weight_df.loc[((weight_df['Sport'] == "Gymnastics") & (weight_df['In team?'] == '')), ['In team?','Event weight']] = 'No', 1
weight_df.loc[((weight_df['Sport'] == "Swimming") & (weight_df['In team?'] == '')), ['In team?','Event weight']] = 'No', 1

In [21]:
# Ajustes finos
# ESPECIFICAMENTE EM 1948, O PESO PARA "Basketball Men's Basketball" É 1/10
# CORRIGE-SE LOGO À FRENTE, APÓS OS MERGES
weight_df.loc[weight_df['Event'] == "Basketball Men's Basketball", 'Event weight'] = 1/12 

weight_df.loc[weight_df['Event'] == "Basketball Women's Basketball", 'Event weight'] = 1/12
weight_df.loc[weight_df['Event'] == "Equestrianism Mixed Jumping, Team", 'Event weight'] = 1/4

weight_df.loc[weight_df['Sport'] == "Volleyball", 'Event weight'] = 1/12

In [22]:
weight_df = weight_df.drop(columns = ['Sport'])

In [23]:
# Verificação de quais não tiveram ainda peso associado
# Terão esse valor associado em seguida
weight_df[weight_df['Event weight'] == '']

Event In team? Event weight
22    Football Men's Football      Yes             
23  Football Women's Football      Yes

In [24]:
# Dataframe com os pesos por medalhas
med_weight = pd.DataFrame({'Medal':['Gold', 'Silver', 'Bronze'], 'Medal weight':[3,2,1]})
med_weight

Medal  Medal weight
0    Gold             3
1  Silver             2
2  Bronze             1

In [25]:
# Inclusão dos pesos das medalhas no dataframe principal e reordenação das colunas
birth_med_BR = pd.merge((pd.merge(birth_med_BR, med_weight, on='Medal')),weight_df, on='Event')
birth_med_BR = birth_med_BR.iloc[:,[0,1,2,3,4,5,6,7,10,11,8,9]]

In [26]:
# Ajustes finais nos pesos
birth_med_BR.loc[((birth_med_BR['Event'] == "Football Men's Football") & (birth_med_BR['Year'] == 1984)), 'Event weight'] = 1/16
birth_med_BR.loc[((birth_med_BR['Event'] == "Football Men's Football") & (birth_med_BR['Year'] == 1988)), 'Event weight'] = 1/16
birth_med_BR.loc[((birth_med_BR['Event'] == "Football Men's Football") & (birth_med_BR['Year'] == 1996)), 'Event weight'] = 1/17
birth_med_BR.loc[((birth_med_BR['Event'] == "Football Women's Football") & (birth_med_BR['Year'] == 2004)), 'Event weight'] = 1/17
birth_med_BR.loc[((birth_med_BR['Event'] == "Football Women's Football") & (birth_med_BR['Year'] == 2008)), 'Event weight'] = 1/18
birth_med_BR.loc[((birth_med_BR['Event'] == "Football Men's Football") & (birth_med_BR['Year'] == 2008)), 'Event weight'] = 1/17
birth_med_BR.loc[((birth_med_BR['Event'] == "Football Men's Football") & (birth_med_BR['Year'] == 2012)), 'Event weight'] = 1/19
birth_med_BR.loc[((birth_med_BR['Event'] == "Football Men's Football") & (birth_med_BR['Year'] == 2016)), 'Event weight'] = 1/17
birth_med_BR.loc[((birth_med_BR['Event'] == "Football Men's Football") & (birth_med_BR['Year'] == 2020)), 'Event weight'] = 1/22

# ESPECIFICAMENTE PARA O ANO 2000, O PESO DE "Athletics Men's 4 x 100 metres Relay" DEVERÁ SER 1/5, EM VEZ DE 1/4
birth_med_BR.loc[((birth_med_BR['Event'] == "Athletics Men's 4 x 100 metres Relay") & (birth_med_BR['Year'] == 2000)), 'Event weight'] = 1/5

# ESPECIFICAMENTE EM 1948, O PESO PARA "Basketball Men's Basketball" É 1/10
birth_med_BR.loc[((birth_med_BR['Event'] == "Basketball Men's Basketball") & (birth_med_BR['Year'] == 1948)), 'Event weight'] = 1/10

In [27]:
# Inclusão da coluna birth_med_BR['Pond weight'], contendo os pesos baseados em medalha e equipe
birth_med_BR['Pond weight'] = birth_med_BR['Event weight'] * birth_med_BR['Medal weight']

In [28]:
# Inclusão do nome do Estado de origem, das regiões e das siglas
# Reordenação das colunas
# OBSERVAÇÃO: esta inclusão da UF, região e sigla, poderia ter sido feita, sem prejuízos, 
# no momento do merge com o dataframe name_for_corr
# Seria também possível já fazer essa associação no Dataframe name_for_corr, antes do merge
# Eis uma sugestão para uma versão posterior
UF_region = pd.DataFrame({'Birthplace_UF':['Paraná', 'Santa Catarina', 'Rio Grande do Sul',
                                          'São Paulo', 'Minas Gerais', 'Espírito Santo', 'Rio de Janeiro',
                                          'Bahia', 'Sergipe', 'Alagoas', 'Pernambuco', 'Paraíba',
                                          'Rio Grande do Norte', 'Ceará', 'Piauí', 'Maranhão',
                                          'Pará', 'Amapá', 'Amazonas', 'Roraima', 'Acre', 'Rondônia', 'Tocantins',
                                          'Mato Grosso', 'Mato Grosso do Sul', 'Goiás', 'Distrito Federal',
                                          'Exterior'],
                         'Region':['Sul', 'Sul','Sul',
                                  'Sudeste', 'Sudeste', 'Sudeste', 'Sudeste',
                                  'Nordeste', 'Nordeste', 'Nordeste', 'Nordeste', 'Nordeste',
                                  'Nordeste', 'Nordeste', 'Nordeste', 'Nordeste',
                                  'Norte','Norte','Norte','Norte','Norte','Norte','Norte',
                                  'Centro-Oeste', 'Centro-Oeste', 'Centro-Oeste', 'Centro-Oeste',
                                  'Exterior'],
                         'Former Region':['Sul', 'Sul','Sul',
                                  'Sul', 'Leste', 'Leste', 'Leste',
                                  'Leste', 'Leste', 'Nordeste', 'Nordeste', 'Nordeste',
                                  'Nordeste', 'Nordeste', 'Nordeste', 'Nordeste',
                                  'Norte','Norte','Norte','Norte','Norte','Norte','Centro-Oeste',
                                  'Centro-Oeste', 'Centro-Oeste', 'Centro-Oeste', 'Centro-Oeste',
                                         'Exterior'],
                         'Birthplace_2L':['PR', 'SC', 'RS',
                                         'SP', 'MG', 'ES', 'RJ',
                                         'BA', 'SE', 'AL', 'PE', 'PB',
                                         'RN', 'CE', 'PI', 'MA',
                                         'PA', 'AP', 'AM', 'RR', 'AC', 'RO', 'TO',
                                         'MT', 'MS', 'GO', 'DF',
                                         'EX']})
birth_med_BR = pd.merge(birth_med_BR, UF_region, on='Birthplace_UF')
birth_med_BR = birth_med_BR.iloc[:,[0,1,2,3,13,15,14,4,5,6,7,8,9,10,11,12]]
birth_med_BR

Name Sex     Birthplace  \
0                              Ademir Roque Kaefer   M         Toledo   
1                              Ademir Roque Kaefer   M         Toledo   
2    Alexandre "Alexandre Pato" Rodrigues da Silva   M    Pato Branco   
3               Leandro Damião da Silva dos Santos   M  Jardim Alegre   
4                          José Carlos Cracco Neto   M      Paranavaí   
..                                             ...  ..            ...   
499                                 Sebastião Wolf   M   Gößweinstein   
500                   Flávio Vianna De Ulhôa Canto   M         Oxford   
501                                Burkhard Cordes   M      Darmstadt   
502                        Rodrigo de Paula Pessoa   M          Paris   
503                        Rodrigo de Paula Pessoa   M          Paris   

    Birthplace_UF    Region Birthplace_2L Former Region  Year            City  \
0          Paraná       Sul            PR           Sul  1984     Los Angeles   
1          Paraná       Sul            PR           Sul  1988           Seoul   
2          Paraná       Sul            PR           Sul  2012          London   
3          Paraná       Sul            PR           Sul  2012          London   
4          Paraná       Sul            PR           Sul  2016  Rio de Janeiro   
..            ...       ...           ...           ...   ...             ...   
499      Exterior  Exterior            EX      Exterior  1920       Antwerpen   
500      Exterior  Exterior            EX      Exterior  2004          Athina   
501      Exterior  Exterior            EX      Exterior  1968     Mexico City   
502      Exterior  Exterior            EX      Exterior  1996         Atlanta   
503      Exterior  Exterior            EX      Exterior  2000          Sydney   

             Sport                                        Event In team?  \
0         Football                      Football Men's Football      Yes   
1         Football                      Football Men's Football      Yes   
2         Football                      Football Men's Football      Yes   
3         Football                      Football Men's Football      Yes   
4         Football                      Football Men's Football      Yes   
..             ...                                          ...      ...   
499       Shooting  Shooting Men's Free Pistol, 50 metres, Team       No   
500           Judo                 Judo Men's Half-Middleweight       No   
501        Sailing  Sailing Mixed Two Person Heavyweight Dinghy      Yes   
502  Equestrianism            Equestrianism Mixed Jumping, Team      Yes   
503  Equestrianism            Equestrianism Mixed Jumping, Team      Yes   

    Event weight   Medal  Medal weight Pond weight  
0         0.0625  Silver             2       0.125  
1         0.0625  Silver             2       0.125  
2       0.052632  Silver             2    0.105263  
3       0.052632  Silver             2    0.105263  
4       0.058824    Gold             3    0.176471  
..           ...     ...           ...         ...  
499            1  Bronze             1           1  
500            1  Bronze             1           1  
501          0.5  Bronze             1         0.5  
502         0.25  Bronze             1        0.25  
503         0.25  Bronze             1        0.25  

[504 rows x 16 columns]

## Mapa com pesos das contribuições de cada Estado

In [29]:
# Duas mudanças nos nomes das cidades, apenas porque elas não constam na lista de municípios do IBGE
birth_med_BR.loc[birth_med_BR['Birthplace'] == 'Justinópolis', 'Birthplace'] = 'Ribeirão das Neves'

In [30]:
# Cada Estado, região atual, região antiga e município, ganha uma pivot_table contendo o seu nome e a soma de todos os
# pesos por medalhas obtidos
wt_by_UF = pd.pivot_table(data = birth_med_BR,index = 'Birthplace_UF', aggfunc='sum', values='Pond weight').sort_values(by = 'Pond weight', ascending = False)
wt_by_reg = pd.pivot_table(data = birth_med_BR,index = 'Region', aggfunc='sum', values='Pond weight').sort_values(by = 'Pond weight', ascending = False)
wt_by_f_reg = pd.pivot_table(data = birth_med_BR,index = 'Former Region', aggfunc='sum', values='Pond weight').sort_values(by = 'Pond weight', ascending = False)
wt_by_mun = pd.pivot_table(data = birth_med_BR,index = 'Birthplace', aggfunc='sum', values='Pond weight').sort_values(by = 'Pond weight', ascending = False)

# Para se mostrar apenas municípios em que houve ou não houve um medalhista: (retirada dos pesos)
wt_by_mun_nl = wt_by_mun.copy()
wt_by_mun_nl['Pond weight'] = 1000
wt_by_mun_nl = wt_by_mun_nl.rename(columns = {'Pond weight':'Has medal'})

In [31]:
# Nos geodataframes, trocam-se os nomes de algumas colunas, para facilitar os merges
mapa_UF = mapa_UF.rename(columns= {'Estado':'Birthplace_UF'})
mapa_reg = mapa_reg.rename(columns = {'Região atual':'Region'})
mapa_mun = mapa_mun.rename(columns = {'Município':'Birthplace'})

In [32]:
# Definições das funções que serão usadas para se mostrar os mapas

# Função para mostrar o mapa por Estados ou o mapa por regiões:
def nivel_sup(level_name):
    titulo_geral = ('Mapa de distribuição das medalhas ' + level_name + ' de origem dos medalhistas' + '\nRepresentação por pesos das medalhas').replace(' Por ',' por ')
    if level_name == 'Por Estados':
        pd.merge(mapa_UF, wt_by_UF, on='Birthplace_UF', how='left').plot(column='Pond weight', 
                                                                         cmap='Wistia', edgecolor='black', linewidth=.5, figsize=(15,15),
                                                                        legend=True, 
                                                                         legend_kwds={'label':'Somatório dos pesos por Estado',
                                                                                     'orientation':'horizontal',
                                                                                     'shrink':.75}, ax = mapa_UF.plot(figsize=(15,15), color='lightyellow', 
                                                                                                                     edgecolor='black'));
        plt.title(label = titulo_geral, fontweight='bold', fontsize=14)
        plt.show()
        wt_by_UF.head(10)
        
    elif level_name == 'Por regiões':
        pd.merge(mapa_reg, wt_by_reg, on='Region', how='left').plot(column='Pond weight', 
                                                                         cmap='Wistia', edgecolor='black', linewidth=.5, figsize=(15,15),
                                                                        legend=True, 
                                                                         legend_kwds={'label':'Somatório dos pesos por região',
                                                                                     'orientation':'horizontal',
                                                                                     'shrink':.75});
        plt.title(label = titulo_geral, fontweight='bold', fontsize=14)
        plt.show()
        wt_by_reg

In [33]:
# Função para mostrar o mapa por município, com diferentes graus de detalhamento:
def mun_UF(l_mun_uf):
    titulo_geral = 'Municípios que já tiveram ao menos 1 medalhista olímpico\nSeparação por Estado\nApenas ' + l_mun_uf
    sigla = list(UF_region[UF_region['Birthplace_UF'] == l_mun_uf]['Birthplace_2L'])
    mapa_mun[mapa_mun['SIGLA_UF'].isin(sigla)].plot(column='Has medal', cmap='Wistia', edgecolor='black', linewidth=.2, figsize=(10,10), legend=False);
    plt.title(label = titulo_geral, fontweight='bold', fontsize=14)
    if l_mun_uf == 'Espírito Santo':
        plt.xlim(right= -38.5)
    plt.show()

def mun_reg(l_mun_reg):
    titulo_geral = 'Municípios que já tiveram ao menos 1 medalhista olímpico\nSeparação por região\nApenas ' + l_mun_reg
    lista_poss = list(UF_region[UF_region['Region'] == l_mun_reg]['Birthplace_2L'])
    mapa_mun[mapa_mun['SIGLA_UF'].isin(lista_poss)].plot(column='Has medal', cmap='Wistia', edgecolor='black', linewidth=.2, figsize=(10,10), legend=False);
    plt.title(label = titulo_geral, fontweight='bold', fontsize=14)
    if l_mun_reg == 'Sudeste':
        plt.xlim(right= -38.5)
    plt.show();

def nivel_mun(level_mun):
    titulo_geral = 'Municípios que já tiveram ao menos 1 medalhista olímpico'
    if level_mun=='Todo o país':
        titulo_geral = titulo_geral + '\n' + level_mun
        mapa_mun.plot(column='Has medal', cmap='Wistia', edgecolor='black', linewidth=.2, figsize=(10,10), legend=False);
        plt.title(label = titulo_geral, fontweight='bold', fontsize=14)
        plt.show();
        wt_by_mun_nl.head(10)
    
    elif level_mun=='Por Estado':
        print('\033[1m','Qual Estado deseja visualizar?','\033[0m')
        level_uf = widgets.Dropdown(options = lista_UF)
        widgets.interact(mun_UF, l_mun_uf=level_uf);
    
    elif level_mun=='Por região':
        print('\033[1m','Qual região deseja visualizar?','\033[0m')
        level_reg = widgets.Dropdown(options = lista_reg)
        widgets.interact(mun_reg, l_mun_reg=level_reg);

In [34]:
# Mapas feitos com widgets

# Primeiro mapa: mapas de detalhamento por região (atual) ou por Estado
print('\033[1m' + 'Selecione o nível de detalhamento desejado para visualizar o mapa: (Estados/regiões)' + '\033[0m')
level1 = widgets.Dropdown(options=['Por Estados', 'Por regiões'])
widgets.interact(nivel_sup, level_name=level1);

Selecione o nível de detalhamento desejado para visualizar o mapa: (Estados/regiões)


interactive(children=(Dropdown(description='level_name', options=('Por Estados', 'Por regiões'), value='Por Es…

In [35]:
# Segundo mapa: mapa com seleções detalhadas dos municípios

In [36]:
# Alteração do geodataframe mapa_mun, para incluir quais cidades possuem ou não medalhistas
mapa_mun = pd.merge(mapa_mun, wt_by_mun_nl, on='Birthplace', how='left')
mapa_mun.loc[mapa_mun['Has medal'].isna(), 'Has medal'] = 0

In [37]:
# Regiões e Estados que poderão ser selecionados
lista_UF = sorted(list(UF_region[UF_region['Birthplace_UF'] != 'Exterior']['Birthplace_UF']), key=locale.strxfrm)
lista_reg = sorted(list(UF_region[UF_region['Region'] != 'Exterior']['Region'].unique()), key=locale.strxfrm)

In [38]:
# Chamada do widget para o segundo mapa
print('\033[1m' + 'Selecione o nível de detalhamento desejado para visualizar o mapa por municípios:' + '\033[0m')
level2 = widgets.Dropdown(options=['Todo o país','Por Estado', 'Por região'])
widgets.interact(nivel_mun, level_mun=level2);

Selecione o nível de detalhamento desejado para visualizar o mapa por municípios:


interactive(children=(Dropdown(description='level_mun', options=('Todo o país', 'Por Estado', 'Por região'), v…

## Gráfico de barchart race

In [39]:
# Preparação para o gráfico por Estado
df_yr_UF = birth_med_BR.groupby(['Year', 'Birthplace_UF']).size().reset_index(name = 'Total_UF')
df_yr_UF['Year'] = pd.to_datetime(df_yr_UF['Year'], format='%Y')
df_yr_UF = df_yr_UF.pivot_table(index='Year', columns='Birthplace_UF', values='Total_UF', aggfunc=np.sum, fill_value=0)
df_yr_UF = df_yr_UF.cumsum()

In [40]:
# Preparação para o gráfico por Região
df_yr_Reg = birth_med_BR.groupby(['Year', 'Region']).size().reset_index(name = 'Total_Region')
df_yr_Reg['Year'] = pd.to_datetime(df_yr_Reg['Year'], format='%Y')
df_yr_Reg = df_yr_Reg.pivot_table(index='Year', columns='Region', values='Total_Region', aggfunc=np.sum, fill_value=0)
df_yr_Reg = df_yr_Reg.cumsum()

In [41]:
# Separação apenas das capitais e das cidades metropolitanas
lista_cap_met = [
'Rio Branco',
'Maceió',
'Manaus',
'Salvador',
'Brasília',
'Vitória',
'Goiânia',
'São Luís',
'Campo Grande',
'Belo Horizonte',
'Curitiba',
'João Pessoa',
'Belém',
'Recife',
'Teresina',
'Natal',
'Porto Alegre',
'Rio de Janeiro',
'Boa Vista',
'Florianópolis',
'Aracaju',
'São Paulo',
'Ananindeua',
'Canoas',
'Carapicuíba',
'Ceilândia',
'Contagem',
'Cotia',
'Guarulhos',
'Mauá',
'Mogi das Cruzes',
'Niterói',
'Novo Hamburgo',
'Osasco',
'Santo André',
'São Bernardo do Campo',
'São Caetano do Sul',
'São João de Meriti',
'São Leopoldo',
'Suzano',
'Viamão'
]

In [42]:
# Preparação para o gráfico por cidade
df_yr_ct = birth_med_BR.groupby(['Year', 'Birthplace']).size().reset_index(name = 'Total_City')
df_yr_ct['Year'] = pd.to_datetime(df_yr_ct['Year'], format='%Y')
df_yr_ct = df_yr_ct.pivot_table(index='Year', columns='Birthplace', values='Total_City', aggfunc=np.sum, fill_value=0)
df_yr_ct = df_yr_ct.cumsum()

In [43]:
# Preparação para o gráfico por cidade (excluindo capitais e cidades metropolitanas)
birth_med_BR['Birthplace_int'] = birth_med_BR['Birthplace'] + ' - ' + birth_med_BR['Birthplace_2L']
df_yr_ct_int = birth_med_BR[~(birth_med_BR['Birthplace'].isin(lista_cap_met))].groupby(['Year', 'Birthplace_int']).size().reset_index(name = 'Total_City')
df_yr_ct_int['Year'] = pd.to_datetime(df_yr_ct_int['Year'], format='%Y')
df_yr_ct_int = df_yr_ct_int.pivot_table(index='Year', columns='Birthplace_int', values='Total_City', aggfunc=np.sum, fill_value=0)
df_yr_ct_int = df_yr_ct_int.cumsum()
birth_med_BR = birth_med_BR.drop(columns = ['Birthplace_int'])

In [44]:
# Aqui criou-se uma lista de cores customizada para representar cada UF, não apenas usando-se cores aleatórias
colors_UF = ['greenyellow',
'indigo',
'salmon',
'red',
'lightgreen',
'pink',
'lightgray',
'yellow',
'maroon',
'cornflowerblue',
'lightcoral',
'g',
'brown',
'crimson',
'darkblue',
'lawngreen',
'forestgreen',
'orangered',
'lightskyblue',
'turquoise',
'lime',
'olive',
'k'
]

In [45]:
p_len = 700
st_per = 40
titulo_grafico = "Estados de origem dos medalhistas olímpicos do Brasil" + chr(10) + "Entre " + str(min(birth_med_BR['Year'])) + " e " + str(max(birth_med_BR['Year'])) + ' - Quantidade de medalhas'



bcr.bar_chart_race(df=df_yr_UF, filename=None, title = titulo_grafico, n_bars = 10,
                 period_length = p_len, steps_per_period = st_per,
                  period_fmt = '%Y', cmap=colors_UF,
                  filter_column_colors = False, dpi=144*2,
                  bar_kwargs={'alpha':1})

In [46]:
p_len = 700
st_per = 40
titulo_grafico = "Regiões de origem dos medalhistas olímpicos do Brasil" + chr(10) + "Entre " + str(min(birth_med_BR['Year'])) + " e " + str(max(birth_med_BR['Year'])) + ' - Quantidade de medalhas'



bcr.bar_chart_race(df=df_yr_Reg, filename=None, title = titulo_grafico, n_bars = 5,
                 period_length = p_len, steps_per_period = st_per,
                  period_fmt = '%Y', cmap= ['cadetblue', 'lightgray','darkkhaki','darkgreen','dimgrey','darkblue'],
                  filter_column_colors = False, dpi=144*2,
                  bar_kwargs={'alpha':1})

In [47]:
p_len = 700
st_per = 40
titulo_grafico = "Cidades de origem dos medalhistas olímpicos do Brasil" + chr(10) + "Entre " + str(min(birth_med_BR['Year'])) + " e " + str(max(birth_med_BR['Year'])) + ' - Quantidade de medalhas'



bcr.bar_chart_race(df=df_yr_ct, filename=None, title = titulo_grafico, n_bars = 10,
                 period_length = p_len, steps_per_period = st_per,
                  period_fmt = '%Y', cmap='Dark2_r',
                  filter_column_colors = True, dpi=144*2,
                   shared_fontdict={'family':'Arial', 'weight':'bold'})

In [48]:
p_len = 700
st_per = 40
titulo_grafico = "Cidades de origem dos medalhistas olímpicos do Brasil" + chr(10) + "Entre " + str(min(birth_med_BR['Year'])) + " e " + str(max(birth_med_BR['Year'])) + ' - Quantidade de medalhas' + chr(10) + '(Excluindo-se capitais e cidades das suas regiões metropolitanas)'



bcr.bar_chart_race(df=df_yr_ct_int, filename=None, title = titulo_grafico, n_bars = 15,
                 period_length = p_len, steps_per_period = st_per,
                  period_fmt = '%Y', cmap='Dark2',
                  filter_column_colors = True, dpi=144*2,
                   shared_fontdict={'family':'Arial', 'weight':'bold'})

In [49]:
p_len = 700
st_per = 40
titulo_grafico = "Cidades de origem dos medalhistas olímpicos do Brasil" + chr(10) + "Entre " + str(min(birth_med_BR['Year'])) + " e " + str(max(birth_med_BR['Year'])) + ' - Quantidade de medalhas' + chr(10) + '(Excluindo-se capitais e cidades das suas regiões metropolitanas)'



bcr.bar_chart_race(df=df_yr_ct_int, filename='Medalhistas_por_cidade_interior.mp4', title = titulo_grafico, n_bars = 15,
                 period_length = p_len, steps_per_period = st_per,
                  period_fmt = '%Y', cmap='Dark2',
                  filter_column_colors = True, dpi=144*2,
                   shared_fontdict={'family':'Arial', 'weight':'bold'})